# Food Network

## Begin

In [10]:
# Import statements
import os
import ast
import sys
import glob
import json
import time
import asyncio
import pandas as pd
from bs4 import BeautifulSoup
from urllib.request import Request, urlopen

### Constants

In [165]:
# Get Current Directory Path
PATH = os.getcwd()
# URL to the website
INDEX_URL = "http://www.foodnetwork.com/recipes/recipes-a-z"
# URL to the reviews for recipe
REVIEW_INDEX_URL = "https://api.sni.foodnetwork.com/moderation-chitter-proxy/v1/comments/brand/FOOD/type/recipe/id/"
# Directory for list of recipes
RECIPE_LIST_DIR = PATH + "/datasets/food-network/recipe-lists/"
# Directory for recipes csv
RECIPE_DIR = PATH + "/datasets/food-network/recipes/"
# Directory for list of reviews 
REVIEW_LIST_DIR = PATH + "/datasets/food-network/review-lists/"
# Director for reviews
REVIEW_DIR = PATH + "/datasets/food-network/reviews/"

### Common Methods

In [3]:
# Make Directory if does not exist
def make_check_directory(dir_path):
    if not os.path.exists(dir_path):
        os.makedirs(dir_path)

In [4]:
def get_web_content(url):
    # Open the url and read
    try:
        request = Request(url, headers={'User-Agent': 'Mozilla/5.0'})
        webContent = urlopen(request).read().decode('UTF-8')
        return webContent
    except Exception as e:
        print("Error in requesting web page: ", e)
        raise

In [242]:
make_check_directory(RECIPE_DIR)
make_check_directory(RECIPE_LIST_DIR)
make_check_directory(REVIEW_LIST_DIR)
make_check_directory(REVIEW_DIR)

## Get the Recipes List

In [577]:
# Save file with every recipe in one initial page.
async def save_recipes_list(recipes_url, title):
    # List for all recipes in this initial
    final_recipe_list = []
    try:
        # Open the url and read 
        web_content = get_web_content(recipes_url)
        # Parse the file and get the html content in beautiful soup type
        html_content = BeautifulSoup(web_content, 'html.parser')
        # Get the section containing pagination for the page.
        a_to_z = html_content.find('div', class_="aToZ section")
        # Get the pagination section
        pages = a_to_z.find_all("a", class_="o-Pagination__a-Button")
        # Get the last number of page
        last_page = pages[-2]
        last_page = last_page.text
        # Get the title and link of all recipes in this initial
        for i in range(1, int(last_page)+1):
            try:
                # URL for paginated webpage
                page_url = recipes_url+"/p/"+str(i)
                # Request the URL
                req = Request(page_url, headers={'User-Agent': 'Mozilla/5.0'})
                w_content = urlopen(req).read().decode('UTF-8')
                # Parse the web content and get the html content in beautiful soup type
                page_content = BeautifulSoup(w_content, 'html.parser')
                # Find all the columns containing recipes
                recipe_list = page_content.find_all('ul', class_ = "m-PromoList o-Capsule__m-PromoList")
                # Recipes list
                recipes = []
                # Get all the sections of recipes in this webpage
                for element in recipe_list:
                    recipes = recipes + element.find_all('li', class_ ="m-PromoList__a-ListItem")
                # For all recipes found in this intial add to list
                for recipe in recipes:
                    # Get the link of this recipe
                    recipe_link = "https:"+recipe.a['href']
                    # Get the title of this recipe
                    recipe_title = recipe.a.text
                    recipe_title = recipe_title.replace("/", " ")
                    # Saving the recipe file
                    final_recipe_list.append([recipe_title, recipe_link])
            except Exception:
                print("Error in getting the recipes in pagination")
                raise
        # Return all the recipes in this initial
        return final_recipe_list
    except Exception:
        print("Error in getting the initial web page")
        raise

In [578]:
# Find all the recipes for each initial
async def get_links(url):
    # List of columns
    columns = ['recipe_title','recipe_url']
    # DataFrame 
    food_network_df = pd.DataFrame([], columns=columns)
    # Open the url and read 
    webContent = get_web_content(url)
     # Parse the file and get the html content in beautiful soup type
    html_soup = BeautifulSoup(webContent, 'html.parser')
    # Find the pagination element
    initials_list = html_soup.find('ul', class_ = "o-IndexPagination__m-List")
    # Get links for all the initials
    initials = initials_list.find_all('a', class_ ="o-IndexPagination__a-Button")
    # Get recipes in each initial
    for initial in initials:
        # Link for the initial 
        link = "https:"+initial['href']
        # Initial Title
        title = initial.text
        print("Starting to collect recipes starting with ", title)
        try:
            recipes_list = await save_recipes_list(link, title)
            initial_df = pd.DataFrame(recipes_list, columns=columns)
            initial_df.to_csv(RECIPE_LIST_DIR+title+'.csv', index=True)
            print("Completed saving recipes starting with ", title)
        except Exception as e:
            print("Error occured in saving recipe starting with ", title)
            print("Error Message: ", str(e))
    # Success Message
    print("#######################")
    print("Successfully completed!")
    print("#######################")

In [579]:
# Get Csv with all links and title
await get_links(INDEX_URL)

Starting to collect recipes starting with  123
Completed saving recipes starting with  123
Starting to collect recipes starting with  A
Completed saving recipes starting with  A
Starting to collect recipes starting with  B
Completed saving recipes starting with  B
Starting to collect recipes starting with  C
Completed saving recipes starting with  C
Starting to collect recipes starting with  D
Completed saving recipes starting with  D
Starting to collect recipes starting with  E
Completed saving recipes starting with  E
Starting to collect recipes starting with  F
Completed saving recipes starting with  F
Starting to collect recipes starting with  G
Completed saving recipes starting with  G
Starting to collect recipes starting with  H
Completed saving recipes starting with  H
Starting to collect recipes starting with  I
Completed saving recipes starting with  I
Starting to collect recipes starting with  J
Completed saving recipes starting with  J
Starting to collect recipes starting wi

## Get the Recipes 

In [160]:
# Columns for the final dfs
recipe_columns = ['id', 'name', 'time_taken', 'servings', 'ingredients', 'directions', 'categories']
review_list_columns = ['id', 'unique_id']
review_columns = ['username', 'rating', 'review_date', 'recipe_id', 'review_text']

### Web Scraping each recipe

In [9]:
# Reading each recipe
# Output: Returns a dataframe containing information about the given recipe
def read_recipe(url):
    
    try:
        # Get the html page
        webContent = get_web_content(url)
        # Parse the html page
        soup = BeautifulSoup(webContent, 'html.parser')
        
        # Start scraping information

        # Empty data list
        data = []
        
        recipe_id = url.split('-')[-1]
        data.append(recipe_id)
        
        # Recipe content
        recipe_content = soup.find('div', class_ = "content-well")

        # Summary of the recipe
        recipe_summary = recipe_content.find("div", class_ = "review-summary")

        # Recipe Info
        recipe_info = recipe_content.find('div', class_ = "recipeInfo")

        # Recipe Body
        recipe_body = recipe_content.find('div', class_="recipe-body")

        # Title of recipe
        recipe_title = recipe_content.find('span', class_ = "o-AssetTitle__a-HeadlineText")
        if recipe_title != None:
            recipe_title = recipe_title.text
        else:
            recipe_title = ""
        data.append(recipe_title)

        # Time taken to cook recipe
        recipe_time = recipe_info.find('span', class_ = "o-RecipeInfo__a-Description m-RecipeInfo__a-Description--Total")
        if recipe_time != None:
            recipe_time = recipe_time.text.strip()
        else: 
            recipe_time = ""
        data.append(recipe_time)

        # Total servings per recipe
        recipe_yield = recipe_info.find('ul', class_ = "o-RecipeInfo__m-Yield")
        if recipe_yield != None:
            recipe_yield = recipe_yield.find('span', class_ = "o-RecipeInfo__a-Description")
            if recipe_yield != None:
                recipe_yield = recipe_yield.text.split(" ")[0].strip()
            else:
                recipe_yield = ""
        else:
                recipe_yield = ""
        data.append(recipe_yield)

        # Ingredients
        recipe_ingredients = []
        recipe_ingredients_body = recipe_body.find('div', class_="o-Ingredients__m-Body")
        if recipe_ingredients_body != None:
            recipe_ingredients_body = recipe_ingredients_body.find_all('p', class_="o-Ingredients__a-Ingredient")[1:]
            for ingredient in recipe_ingredients_body:
                recipe_ingredient = ingredient.find('span', class_="o-Ingredients__a-Ingredient--CheckboxLabel").text
                if recipe_ingredient != None:    
                    recipe_ingredients.append(recipe_ingredient)
        data.append(recipe_ingredients)

        # Recipe Steps
        recipe_steps = []
        recipe_description = recipe_body.find('div', class_="o-Method__m-Body")
        if recipe_description != None:
            recipe_description = recipe_description.find_all('li', class_="o-Method__m-Step")
            for step in recipe_description:
                if step != None:
                    recipe_steps.append(step.text.strip())
        data.append(recipe_steps)

        # Recipe Categories
        recipe_categories = []
        recipe_body_footer = recipe_content.find('div', class_='recipe-body-footer')
        if recipe_body_footer != None:
            recipe_category_list = recipe_body_footer.find('div', class_='o-Capsule__m-TagList m-TagList')
            if recipe_category_list != None:
                recipe_category_list = recipe_category_list.find_all('a', class_='o-Capsule__a-Tag a-Tag')
                for category in recipe_category_list:
                    if category != None:
                        recipe_categories.append(category.text.strip())
        data.append(recipe_categories)
        
        review_df = pd.DataFrame([], columns=review_list_columns)
        
        # Get the review - ratings Id
        div = soup.find('div', class_='o-ReviewSummary')
        if div != None:
            rating_section = div.find('script')
            if rating_section != None:
                json_data =  json.loads(rating_section.text)
                unique_id = json_data['assetId']
                review_df = pd.DataFrame([[recipe_id, unique_id]], columns=review_list_columns)
        
        # Convert the scraped information into dataframes
        recipe_df = pd.DataFrame(data, recipe_columns)
        recipe_df = recipe_df.T
        
        
    except:
        print("Error in reading recipe")
        raise

    # Return the created dataframe
    return recipe_df, review_df

In [10]:
# Get recipes for each letter
async def get_recipes_by_file(file_name):
    recipes_file_df = pd.DataFrame([], columns=recipe_columns)
    reviews_file_df = pd.DataFrame([], columns=review_list_columns)

    input_df = pd.read_csv(file_name)  
    title_list = input_df['recipe_title'].values.tolist()
    links_list = input_df['recipe_url'].values.tolist()

    for i in range(len(links_list)):
        print("Reading " + str(i+1) + " of " + str(len(links_list)) + " recipes" )
        print("Reading recipe: ", title_list[i])
        try:
            recipe, reviews = read_recipe(links_list[i])
            recipes_file_df = pd.concat([recipes_file_df, recipe], ignore_index=True)
            reviews_file_df = pd.concat([reviews_file_df, reviews], ignore_index=True)
        except Exception as e:
            print("Error in reading recipe: ", title_list[i])
            print("Error: ", e)

    return recipes_file_df, reviews_file_df

In [11]:
async def get_recipes():
    filenames = glob.glob(RECIPE_LIST_DIR+"*.csv")
    recipes_df = pd.DataFrame([], columns=recipe_columns)
    reviews_df = pd.DataFrame([], columns=review_list_columns)
    for file in filenames:
        try:
            file_name = file.split('/')[-1]
            file_name = file_name.split('.')[0].strip()
            print("#########################")
            print("Started Reading Recipes starting with ", file_name)
            print("#########################")
            recipes_file_df, reviews_file_df = await get_recipes_by_file(file)
            recipes_file_df.to_csv(RECIPE_DIR+file_name+".csv")
            reviews_file_df.to_csv(REVIEW_LIST_DIR+file_name+".csv")
            print("#########################")
            print("Successfully Completed Reading Recipes starting with ", file_name)
            print("#########################")
        except Exception as e:
            print("Error in reading filename: ", file_name)
            print("Error: ", e)

In [12]:
await get_recipes()

#########################
Started Reading Recipes starting with  123
#########################
Reading 1 of 226 recipes
Reading recipe:  "16 Bean" Pasta E Fagioli
Reading 2 of 226 recipes
Reading recipe:  "16 Bean" Pasta e Fagioli
Reading 3 of 226 recipes
Reading recipe:  "21" Apple Pie
Reading 4 of 226 recipes
Reading recipe:  1 S'more for the Road and Kiddie S'mores
Reading 5 of 226 recipes
Reading recipe:  1-2-3 Lasagna
Reading 6 of 226 recipes
Reading recipe:  1-Step Chipotle Hummus
Reading 7 of 226 recipes
Reading recipe:  10 Minute Apple Sauce
Reading 8 of 226 recipes
Reading recipe:  10 Minute Apple Sauce
Reading 9 of 226 recipes
Reading recipe:  10 Minute Fruit Tart
Reading 10 of 226 recipes
Reading recipe:  10,000 Island Dressing with Layered Salad
Reading 11 of 226 recipes
Reading recipe:  10-Minute Arrabbiata Sauce
Reading 12 of 226 recipes
Reading recipe:  10-Minute Beef-and-Beet Salad with Horseradish Dressing
Reading 13 of 226 recipes
Reading recipe:  10-Minute Chicken, C

Reading 100 of 226 recipes
Reading recipe:  3-D Dog Cake
Reading 101 of 226 recipes
Reading recipe:  3-Ingredient Banana Bread
Reading 102 of 226 recipes
Reading recipe:  3-Ingredient Banana Icebox Cake
Reading 103 of 226 recipes
Reading recipe:  3-Ingredient Banana Petit Fours
Reading 104 of 226 recipes
Reading recipe:  3-Ingredient Banana Pudding
Reading 105 of 226 recipes
Reading recipe:  3-Ingredient Banana, Raspberry and Coconut "Ice Cream"
Reading 106 of 226 recipes
Reading recipe:  3-Ingredient Bundt Cake
Reading 107 of 226 recipes
Reading recipe:  3-Ingredient Cookie Butter Cookies
Reading 108 of 226 recipes
Reading recipe:  3-Ingredient Pumpkin Bread
Reading 109 of 226 recipes
Reading recipe:  3-Layer Sour Cream Cake with Cream Cheese Frosting
Reading 110 of 226 recipes
Reading recipe:  3-Peppercorn Bison with Tennessee Whiskey Sauce
Reading 111 of 226 recipes
Reading recipe:  3-Salad Chef's Salad Plate
Reading 112 of 226 recipes
Reading recipe:  3-Shot Cocktail ("Bandera and 

Reading 205 of 226 recipes
Reading recipe:  6-Minute Egg on Creamy Polenta with Crispy Serrano Ham
Reading 206 of 226 recipes
Reading recipe:  60's Indoor S'Mores with Homemade Graham Crackers
Reading 207 of 226 recipes
Reading recipe:  7 Fishes Fra Diavolo Pasta
Reading 208 of 226 recipes
Reading recipe:  7 Layer Sombrero Dip
Reading 209 of 226 recipes
Reading recipe:  7-Can Soup
Reading 210 of 226 recipes
Reading recipe:  7-Layer Dessert Dip
Reading 211 of 226 recipes
Reading recipe:  7-Layer Deviled Egg Dip
Reading 212 of 226 recipes
Reading recipe:  7-Layer Greek Meze Dip
Reading 213 of 226 recipes
Reading recipe:  7-Layer Italian Hero Dip
Reading 214 of 226 recipes
Reading recipe:  7-Layer Pasta Salad
Reading 215 of 226 recipes
Reading recipe:  7-Layer Salad with Pine Nut Pesto, Bacon and Roasted Beets with Toasty Almonds
Reading 216 of 226 recipes
Reading recipe:  7-Layer Thai Chicken Dip
Reading 217 of 226 recipes
Reading recipe:  7-Minute Frosting
Reading 218 of 226 recipes
Rea

Reading 82 of 499 recipes
Reading recipe:  Yo Halla on the Square
Reading 83 of 499 recipes
Reading recipe:  Yo Yo Yo Fries
Reading 84 of 499 recipes
Reading recipe:  Yogi Tea
Reading 85 of 499 recipes
Reading recipe:  Yogi Tea
Reading 86 of 499 recipes
Reading recipe:  Yogi Wings
Reading 87 of 499 recipes
Reading recipe:  Yogurt Based Sauces
Reading 88 of 499 recipes
Reading recipe:  Yogurt Blini Bar
Reading 89 of 499 recipes
Reading recipe:  Yogurt Braised Leg of Lamb
Reading 90 of 499 recipes
Reading recipe:  Yogurt Braised Leg of Lamb
Reading 91 of 499 recipes
Reading recipe:  Yogurt Cheese
Reading 92 of 499 recipes
Reading recipe:  Yogurt Cheese
Reading 93 of 499 recipes
Reading recipe:  Yogurt Creme Brulee
Reading 94 of 499 recipes
Reading recipe:  Yogurt Creme Brulee with Fresh Fruit and Granola
Reading 95 of 499 recipes
Reading recipe:  Yogurt Creme Brulee with Fresh Fruit and Granola
Reading 96 of 499 recipes
Reading recipe:  Yogurt Creme Brulee with Fresh Fruit and Granola
Re

Reading 193 of 499 recipes
Reading recipe:  Yucca with Cuban Mojo
Reading 194 of 499 recipes
Reading recipe:  Yucca with Garlic Mojo
Reading 195 of 499 recipes
Reading recipe:  Yucca with Garlic Sauce: Yucca con Mojo
Reading 196 of 499 recipes
Reading recipe:  Yukon Gold Colcannon with Sauteed Kale and Cabbage and Bacon Butter
Reading 197 of 499 recipes
Reading recipe:  Yukon Gold Potato Gratin with Horseradish, Gruyere and Sweet Onion
Reading 198 of 499 recipes
Reading recipe:  Yukon Gold Potato Salad with Cherry Peppers and Sweet Relish Vinaigrette
Reading 199 of 499 recipes
Reading recipe:  Yukon Gold Potato Soup with Chive Oil, Beet Reduction and Sweet Garlic Confit Croutons
Reading 200 of 499 recipes
Reading recipe:  Yukon Gold Potatoes: Jacques Pepin Style
Reading 201 of 499 recipes
Reading recipe:  Yukon Gold and Green Chile Hash
Reading 202 of 499 recipes
Reading recipe:  Yule Log
Reading 203 of 499 recipes
Reading recipe:  Yule Log Icebox Cake
Reading 204 of 499 recipes
Readin

Reading 306 of 499 recipes
Reading recipe:  Zingerman's Reuben Sandwich
Reading 307 of 499 recipes
Reading recipe:  Zingertini
Reading 308 of 499 recipes
Reading recipe:  Zip-Quick Country Captain
Reading 309 of 499 recipes
Reading recipe:  Zipper Back Shrimp and Nova Scotia Lobster with Potato, Leek and Gooseberry Hash
Reading 310 of 499 recipes
Reading recipe:  Zipper Back Shrimp and Nova Scotia Lobster with Potato, Leek and Gooseberry Hash
Reading 311 of 499 recipes
Reading recipe:  Zipper Bag Caesar
Reading 312 of 499 recipes
Reading recipe:  Zipper Bag Fruit Salad
Reading 313 of 499 recipes
Reading recipe:  Zipper Bag Overnight Oatmeal
Reading 314 of 499 recipes
Reading recipe:  Zippy Italian Popcorn
Reading 315 of 499 recipes
Reading recipe:  Ziti Baked with Shrimp and Feta Cheese - Greek Style
Reading 316 of 499 recipes
Reading recipe:  Ziti Stufati
Reading 317 of 499 recipes
Reading recipe:  Ziti con Broccoli di Rape e Salsicce (Ziti with Broccoli di Rabe and Sausage)
Reading 3

Reading 420 of 499 recipes
Reading recipe:  Zucchini Saute
Reading 421 of 499 recipes
Reading recipe:  Zucchini Slaw
Reading 422 of 499 recipes
Reading recipe:  Zucchini Snack Pizzas
Reading 423 of 499 recipes
Reading recipe:  Zucchini Sottolio
Reading 424 of 499 recipes
Reading recipe:  Zucchini Spears with Rosemary, Garlic and Lemon
Reading 425 of 499 recipes
Reading recipe:  Zucchini Sticks
Error in reading recipe
Error in reading recipe:  Zucchini Sticks
Error:  'NoneType' object has no attribute 'find'
Reading 426 of 499 recipes
Reading recipe:  Zucchini Stuffed Tomatoes
Reading 427 of 499 recipes
Reading recipe:  Zucchini Stuffed with Wild Mushroom and Pine Nut Quiche
Reading 428 of 499 recipes
Reading recipe:  Zucchini Taco Shells with Beef and Zucchini-Tomato Salsa
Reading 429 of 499 recipes
Reading recipe:  Zucchini Tart
Reading 430 of 499 recipes
Reading recipe:  Zucchini Tomato Sauce with Fat Spaghetti
Reading 431 of 499 recipes
Reading recipe:  Zucchini Vichyssoise
Reading 

## Get the Reviews

In [471]:
# Get the response and return json format
def get_response(url):
    response = urlopen(url)
    data_json = json.loads(response.read())
    return data_json

In [536]:
# Parse the Dataframe
def parse_dataframe(df, recipe_id):
    df_reviews = df.copy()
#     print(df_reviews)
    df_reviews['username'] = df_reviews['userReference'].apply(lambda x: str(x['name']) if x != None else "None")
    df_reviews['rating'] = df_reviews['authorAssetRatings'].apply(lambda x: str(x[0]['value']) if len(x) > 0 else "None")
    df_reviews['review_date'] = df_reviews['timestamp']
    df_reviews['recipe_id'] = str(recipe_id)
    df_reviews['text'] = df_reviews['text'].apply(lambda x: x.replace('<br>', " "))
    df_reviews['text'] = df_reviews['text'].apply(lambda x: x.replace('<br/>', " "))
    df_reviews['text'] = df_reviews['text'].apply(lambda x: x.replace('<br />', " "))
    df_reviews['review_text'] = df_reviews['text'].astype(str)
    df_reviews = df_reviews[review_columns]
    df_reviews.drop_duplicates(subset='review_text', keep="first", inplace=True)
    return df_reviews

In [537]:
def get_reviews(url):
    comments_df = pd.DataFrame()
    has_next = True
    cursor_id = ""
    cursors = []
    while(has_next):
        json_data = get_response(url+"?cursor="+cursor_id)
        page_info = json_data['pageInfo']
        has_next = page_info['hasNextPage']
        try:
            if page_info['endCursor'] not in cursors:
                cursor_id = page_info['endCursor']
                cursors.append(cursor_id)
            else: 
                has_next=False
        except:
            cursor_id = ""
        if "comments" in json_data:
            temp_df = pd.DataFrame(json_data['comments'])
            comments_df = pd.concat([comments_df, temp_df], ignore_index=True)
    return comments_df

In [538]:
def read_reviews(recipe_id, recipe_unique_id):
    print("Reading Recipe Id: ", recipe_id)
    parsed_reviews_df = pd.DataFrame()
    try:
        recipe_url = REVIEW_INDEX_URL+recipe_unique_id
        raw_reviews_df = get_reviews(recipe_url)
        if raw_reviews_df.shape[0] > 0:
            parsed_reviews_df = parse_dataframe(raw_reviews_df, recipe_id)
        print("Successfully Read Recipe Id: ", recipe_id)
    except Exception as e:
        print("Error in reading Recipe Id: ", recipe_id)
        print("Error: ", e)
    return parsed_reviews_df

### Testing the Process

In [539]:
code = "3dd61386-23e6-44cc-9b1e-4929be4ca4c0"
code = "51d106a4-734d-4898-b61b-fc0bda7da58a"
recipe_id = 192929
some_url = "https://api.sni.foodnetwork.com/moderation-chitter-proxy/v1/comments/brand/FOOD/type/recipe/id/"+code
read_reviews(recipe_id, code)

Reading Recipe Id:  192929
Successfully Read Recipe Id:  192929


username rating               review_date recipe_id  \
0      Igor Z.   None  2021-05-27T22:55:18.048Z    192929   
1     Roger D.      2  2014-06-23T01:12:57.000Z    192929   
2        dan_p      5  2012-02-13T17:53:48.000Z    192929   
3  macrophylla      3  2012-01-25T12:04:28.000Z    192929   
4   Oh Momma D      4  2012-01-04T09:03:20.000Z    192929   
5     Joyce K.      5  2011-11-05T12:05:52.000Z    192929   
6  MissKathy#1      4  2011-07-22T20:07:56.000Z    192929   
7      Mari G.      5  2010-03-30T21:18:30.000Z    192929   
8    Sandra H.      5  2010-03-28T14:40:09.000Z    192929   
9     Annie D.      3  2010-03-22T16:26:19.000Z    192929   

                                         review_text  
0  French Meat: Russian recipe without potatoes. ...  
1  Close to Mamere's recipe for tortierre.....I p...  
2      Formidably..Just like in Quebec..Marci bocoup  
3  The pie crust portion of the recipe is awful, ...  
4  This was a very good recipe. There were two ad...  
5  Mr. Morin; This is very good! Thanks for being...  
6  I'm going to make this as an 'American" Meat p...  
7  My self, I would do everything the recipe's ca...  
8  I also like to read the reviews so if I need t...  
9  The cinnamon and nutmeg give the filling a uni...

In [540]:
def read_reviews_by_recipes(filename):
    initial_file_name = filename.split('/')[-1].split(".")[0]
    print("Reading reviews for recipes starting with: ", initial_file_name)
    inital_df = pd.read_csv(filename)
    res_df = pd.DataFrame([], columns=review_columns)
    count = 0
    for row in inital_df.itertuples():
        count += 1
        recipe_id = row.id
        unique_id = row.unique_id
        reviews = read_reviews(recipe_id, unique_id)
        res_df = pd.concat([res_df, reviews], ignore_index=True)
        if count%200 == 0:
            print("Sleeping for 10 Seconds")
            time.sleep(10)
    res_df.to_csv(REVIEW_DIR+initial_file_name+".csv", index=False)
    print("Saved Reviews File for initial: ", initial_file_name)

### Running for one single file

In [541]:
read_reviews_by_recipes(REVIEW_LIST_DIR+"123.csv")

Reading reviews for recipes starting with:  123
Reading Recipe Id:  3612570
Successfully Read Recipe Id:  3612570
Reading Recipe Id:  1925900
Successfully Read Recipe Id:  1925900
Reading Recipe Id:  3644969
Successfully Read Recipe Id:  3644969
Reading Recipe Id:  3416679
Successfully Read Recipe Id:  3416679
Reading Recipe Id:  1938289
Successfully Read Recipe Id:  1938289
Reading Recipe Id:  1920098
Successfully Read Recipe Id:  1920098
Reading Recipe Id:  2103668
Successfully Read Recipe Id:  2103668
Reading Recipe Id:  3363096
Successfully Read Recipe Id:  3363096
Reading Recipe Id:  3363134
Successfully Read Recipe Id:  3363134
Reading Recipe Id:  7532611
Successfully Read Recipe Id:  7532611
Reading Recipe Id:  3363248
Successfully Read Recipe Id:  3363248
Reading Recipe Id:  3362893
Successfully Read Recipe Id:  3362893
Reading Recipe Id:  3362867
Successfully Read Recipe Id:  3362867
Reading Recipe Id:  1949403
Successfully Read Recipe Id:  1949403
Reading Recipe Id:  3416166


Successfully Read Recipe Id:  1945302
Reading Recipe Id:  1937266
Successfully Read Recipe Id:  1937266
Reading Recipe Id:  1937670
Successfully Read Recipe Id:  1937670
Reading Recipe Id:  2013064
Successfully Read Recipe Id:  2013064
Reading Recipe Id:  1956588
Successfully Read Recipe Id:  1956588
Reading Recipe Id:  1941588
Successfully Read Recipe Id:  1941588
Reading Recipe Id:  1942691
Successfully Read Recipe Id:  1942691
Reading Recipe Id:  1938948
Successfully Read Recipe Id:  1938948
Reading Recipe Id:  1944951
Successfully Read Recipe Id:  1944951
Reading Recipe Id:  1921715
Successfully Read Recipe Id:  1921715
Reading Recipe Id:  2125379
Successfully Read Recipe Id:  2125379
Reading Recipe Id:  3645523
Successfully Read Recipe Id:  3645523
Reading Recipe Id:  1950278
Successfully Read Recipe Id:  1950278
Reading Recipe Id:  12343044
Successfully Read Recipe Id:  12343044
Reading Recipe Id:  9604304
Successfully Read Recipe Id:  9604304
Reading Recipe Id:  3414485
Successf

### Running for all files at once

In [543]:
def read_all_reviews():
    filenames = glob.glob(REVIEW_LIST_DIR+"*.csv")
    for file in filenames:
        try:
            read_reviews_by_recipes(file)
        except Exception:
            print("Error in reading the file: ", file)

In [544]:
read_all_reviews()

Reading reviews for recipes starting with:  P
Reading Recipe Id:  1947698
Successfully Read Recipe Id:  1947698
Reading Recipe Id:  2172331
Successfully Read Recipe Id:  2172331
Reading Recipe Id:  1948754
Successfully Read Recipe Id:  1948754
Reading Recipe Id:  1917222
Successfully Read Recipe Id:  1917222
Reading Recipe Id:  2064412
Successfully Read Recipe Id:  2064412
Reading Recipe Id:  1952929
Successfully Read Recipe Id:  1952929
Reading Recipe Id:  2805702
Successfully Read Recipe Id:  2805702
Reading Recipe Id:  2172342
Successfully Read Recipe Id:  2172342
Reading Recipe Id:  2018104
Successfully Read Recipe Id:  2018104
Reading Recipe Id:  9442219
Successfully Read Recipe Id:  9442219
Reading Recipe Id:  4665283
Successfully Read Recipe Id:  4665283
Reading Recipe Id:  1943871
Successfully Read Recipe Id:  1943871
Reading Recipe Id:  1911228
Successfully Read Recipe Id:  1911228
Reading Recipe Id:  1940890
Successfully Read Recipe Id:  1940890
Reading Recipe Id:  2200784
Su

Successfully Read Recipe Id:  2009465
Reading Recipe Id:  1912178
Successfully Read Recipe Id:  1912178
Reading Recipe Id:  1923637
Successfully Read Recipe Id:  1923637
Reading Recipe Id:  2009821
Successfully Read Recipe Id:  2009821
Reading Recipe Id:  1912314
Successfully Read Recipe Id:  1912314
Reading Recipe Id:  11247741
Successfully Read Recipe Id:  11247741
Reading Recipe Id:  3703646
Successfully Read Recipe Id:  3703646
Reading Recipe Id:  1926413
Successfully Read Recipe Id:  1926413
Reading Recipe Id:  1916013
Successfully Read Recipe Id:  1916013
Reading Recipe Id:  1957143
Successfully Read Recipe Id:  1957143
Reading Recipe Id:  2042147
Successfully Read Recipe Id:  2042147
Reading Recipe Id:  1956871
Successfully Read Recipe Id:  1956871
Reading Recipe Id:  1946694
Successfully Read Recipe Id:  1946694
Reading Recipe Id:  1914789
Successfully Read Recipe Id:  1914789
Reading Recipe Id:  1946628
Successfully Read Recipe Id:  1946628
Reading Recipe Id:  1913753
Successf

Successfully Read Recipe Id:  1925862
Reading Recipe Id:  1945454
Successfully Read Recipe Id:  1945454
Reading Recipe Id:  1918216
Successfully Read Recipe Id:  1918216
Reading Recipe Id:  1917172
Successfully Read Recipe Id:  1917172
Reading Recipe Id:  1917172
Successfully Read Recipe Id:  1917172
Reading Recipe Id:  1941301
Successfully Read Recipe Id:  1941301
Reading Recipe Id:  1960045
Successfully Read Recipe Id:  1960045
Reading Recipe Id:  1945013
Successfully Read Recipe Id:  1945013
Reading Recipe Id:  1909248
Successfully Read Recipe Id:  1909248
Reading Recipe Id:  1921425
Successfully Read Recipe Id:  1921425
Reading Recipe Id:  1924675
Successfully Read Recipe Id:  1924675
Reading Recipe Id:  1917352
Successfully Read Recipe Id:  1917352
Reading Recipe Id:  2103133
Successfully Read Recipe Id:  2103133
Reading Recipe Id:  1906479
Successfully Read Recipe Id:  1906479
Reading Recipe Id:  3646139
Successfully Read Recipe Id:  3646139
Reading Recipe Id:  1963428
Successful

Successfully Read Recipe Id:  1942172
Reading Recipe Id:  2394407
Successfully Read Recipe Id:  2394407
Reading Recipe Id:  1956036
Successfully Read Recipe Id:  1956036
Reading Recipe Id:  1910636
Successfully Read Recipe Id:  1910636
Reading Recipe Id:  8037744
Successfully Read Recipe Id:  8037744
Reading Recipe Id:  12145876
Successfully Read Recipe Id:  12145876
Reading Recipe Id:  1960241
Successfully Read Recipe Id:  1960241
Reading Recipe Id:  1948128
Successfully Read Recipe Id:  1948128
Reading Recipe Id:  3645015
Successfully Read Recipe Id:  3645015
Reading Recipe Id:  1912022
Successfully Read Recipe Id:  1912022
Reading Recipe Id:  2013454
Successfully Read Recipe Id:  2013454
Reading Recipe Id:  1951586
Successfully Read Recipe Id:  1951586
Reading Recipe Id:  3361507
Successfully Read Recipe Id:  3361507
Reading Recipe Id:  2102767
Successfully Read Recipe Id:  2102767
Reading Recipe Id:  1959217
Successfully Read Recipe Id:  1959217
Reading Recipe Id:  3065890
Successf

Successfully Read Recipe Id:  1949306
Reading Recipe Id:  9541619
Successfully Read Recipe Id:  9541619
Reading Recipe Id:  2118972
Successfully Read Recipe Id:  2118972
Reading Recipe Id:  2009039
Successfully Read Recipe Id:  2009039
Reading Recipe Id:  8046425
Successfully Read Recipe Id:  8046425
Reading Recipe Id:  5462719
Successfully Read Recipe Id:  5462719
Reading Recipe Id:  1949189
Successfully Read Recipe Id:  1949189
Reading Recipe Id:  1957646
Successfully Read Recipe Id:  1957646
Reading Recipe Id:  3415596
Successfully Read Recipe Id:  3415596
Reading Recipe Id:  1943563
Successfully Read Recipe Id:  1943563
Reading Recipe Id:  2009330
Successfully Read Recipe Id:  2009330
Reading Recipe Id:  1915832
Successfully Read Recipe Id:  1915832
Reading Recipe Id:  1960967
Successfully Read Recipe Id:  1960967
Reading Recipe Id:  2107822
Successfully Read Recipe Id:  2107822
Reading Recipe Id:  2042191
Successfully Read Recipe Id:  2042191
Reading Recipe Id:  10035443
Successfu

...

Successfully Read Recipe Id:  7579631
Reading Recipe Id:  10035490
Successfully Read Recipe Id:  10035490
Reading Recipe Id:  7216795
Successfully Read Recipe Id:  7216795
Reading Recipe Id:  1926548
Successfully Read Recipe Id:  1926548
Reading Recipe Id:  2011846
Successfully Read Recipe Id:  2011846
Reading Recipe Id:  1940227
Successfully Read Recipe Id:  1940227
Reading Recipe Id:  1911920
Successfully Read Recipe Id:  1911920
Reading Recipe Id:  1956815
Successfully Read Recipe Id:  1956815
Reading Recipe Id:  1961232
Successfully Read Recipe Id:  1961232
Reading Recipe Id:  1943914
Successfully Read Recipe Id:  1943914
Reading Recipe Id:  2013933
Successfully Read Recipe Id:  2013933
Reading Recipe Id:  11391172
Successfully Read Recipe Id:  11391172
Reading Recipe Id:  1938760
Successfully Read Recipe Id:  1938760
Reading Recipe Id:  1939110
Successfully Read Recipe Id:  1939110
Reading Recipe Id:  9591277
Successfully Read Recipe Id:  9591277
Reading Recipe Id:  2015095
Succes

Successfully Read Recipe Id:  1910272
Reading Recipe Id:  1965198
Successfully Read Recipe Id:  1965198
Reading Recipe Id:  11931061
Successfully Read Recipe Id:  11931061
Reading Recipe Id:  4664860
Successfully Read Recipe Id:  4664860
Reading Recipe Id:  1946136
Successfully Read Recipe Id:  1946136
Reading Recipe Id:  11659101
Successfully Read Recipe Id:  11659101
Reading Recipe Id:  12146031
Successfully Read Recipe Id:  12146031
Reading Recipe Id:  2105446
Successfully Read Recipe Id:  2105446
Reading Recipe Id:  8362618
Successfully Read Recipe Id:  8362618
Reading Recipe Id:  2270911
Successfully Read Recipe Id:  2270911
Reading Recipe Id:  2042278
Successfully Read Recipe Id:  2042278
Reading Recipe Id:  5660364
Successfully Read Recipe Id:  5660364
Reading Recipe Id:  1961585
Successfully Read Recipe Id:  1961585
Reading Recipe Id:  5389499
Successfully Read Recipe Id:  5389499
Reading Recipe Id:  1962413
Successfully Read Recipe Id:  1962413
Reading Recipe Id:  2011504
Succ

Successfully Read Recipe Id:  3363479
Reading Recipe Id:  1943597
Successfully Read Recipe Id:  1943597
Reading Recipe Id:  7120070
Successfully Read Recipe Id:  7120070
Reading Recipe Id:  10030612
Successfully Read Recipe Id:  10030612
Reading Recipe Id:  1969420
Successfully Read Recipe Id:  1969420
Reading Recipe Id:  1939474
Successfully Read Recipe Id:  1939474
Reading Recipe Id:  1912258
Successfully Read Recipe Id:  1912258
Reading Recipe Id:  1960333
Successfully Read Recipe Id:  1960333
Reading Recipe Id:  2010411
Successfully Read Recipe Id:  2010411
Reading Recipe Id:  1939300
Successfully Read Recipe Id:  1939300
Reading Recipe Id:  2119951
Successfully Read Recipe Id:  2119951
Reading Recipe Id:  3361701
Successfully Read Recipe Id:  3361701
Reading Recipe Id:  1906666
Successfully Read Recipe Id:  1906666
Reading Recipe Id:  1970357
Successfully Read Recipe Id:  1970357
Reading Recipe Id:  1928416
Successfully Read Recipe Id:  1928416
Reading Recipe Id:  1908609
Successf

Successfully Read Recipe Id:  11933101
Reading Recipe Id:  5535086
Successfully Read Recipe Id:  5535086
Reading Recipe Id:  1960626
Successfully Read Recipe Id:  1960626
Reading Recipe Id:  1959166
Successfully Read Recipe Id:  1959166
Reading Recipe Id:  1959078
Successfully Read Recipe Id:  1959078
Reading Recipe Id:  2014372
Successfully Read Recipe Id:  2014372
Reading Recipe Id:  11781806
Successfully Read Recipe Id:  11781806
Reading Recipe Id:  1948311
Successfully Read Recipe Id:  1948311
Reading Recipe Id:  2011557
Successfully Read Recipe Id:  2011557
Reading Recipe Id:  1947452
Successfully Read Recipe Id:  1947452
Reading Recipe Id:  1946779
Successfully Read Recipe Id:  1946779
Reading Recipe Id:  1916102
Successfully Read Recipe Id:  1916102
Reading Recipe Id:  1944363
Successfully Read Recipe Id:  1944363
Reading Recipe Id:  2200971
Successfully Read Recipe Id:  2200971
Reading Recipe Id:  2102413
Successfully Read Recipe Id:  2102413
Reading Recipe Id:  11909162
Succes

Successfully Read Recipe Id:  5196767
Reading Recipe Id:  2109896
Successfully Read Recipe Id:  2109896
Reading Recipe Id:  1912416
Successfully Read Recipe Id:  1912416
Reading Recipe Id:  1914147
Successfully Read Recipe Id:  1914147
Reading Recipe Id:  1956500
Successfully Read Recipe Id:  1956500
Reading Recipe Id:  5523408
Successfully Read Recipe Id:  5523408
Reading Recipe Id:  1951206
Successfully Read Recipe Id:  1951206
Reading Recipe Id:  2365396
Successfully Read Recipe Id:  2365396
Reading Recipe Id:  3690354
Successfully Read Recipe Id:  3690354
Reading Recipe Id:  1955641
Successfully Read Recipe Id:  1955641
Reading Recipe Id:  1908132
Successfully Read Recipe Id:  1908132
Reading Recipe Id:  4695458
Successfully Read Recipe Id:  4695458
Reading Recipe Id:  4695457
Successfully Read Recipe Id:  4695457
Reading Recipe Id:  5312682
Successfully Read Recipe Id:  5312682
Reading Recipe Id:  1973756
Successfully Read Recipe Id:  1973756
Reading Recipe Id:  4695453
Successful

In [547]:
def merge_all_reviews():
    filenames = glob.glob(REVIEW_DIR+"*.csv")
    all_reviews_df = pd.DataFrame([], columns=review_columns)
    for file in filenames:
        try:
            temp_df = pd.read_csv(file, engine='python')
            all_reviews_df = pd.concat([all_reviews_df, temp_df], ignore_index=True)
        except Exception as e:
            print("Error in reading the file: ", file)
            print("Error: ", e)
    all_reviews_df.to_csv("./datasets/food_network_reviews.csv", index=False)
    print("Successfully merged reviews to food_network_reviews")

In [546]:
merge_all_reviews()

Successfully merged reviews to food_network_reviews


### Merging ratings into reviews

In [568]:
def merge_ratings(file_name):
    # Process the reviews dataframe
    try:
        ratings_df = pd.read_csv(REVIEW_DIR+file_name+".csv", engine='python')
        ratings_df = ratings_df.dropna()
        ratings_df = ratings_df[ratings_df['rating'] != "None"]
        ratings_df['rating'] = ratings_df['rating'].astype("float64")
        ratings_df['rating'] = ratings_df['rating'].astype("int64")
        ratings_df = ratings_df[ratings_df['recipe_id'] != None]
        ratings_df['recipe_id'] = ratings_df['recipe_id'].astype(str)
        ratings_df['recipe_id'] = ratings_df['recipe_id'].str.split('.').str[0]    
        ratings_df = ratings_df.groupby('recipe_id').agg(ratings=('rating', 'mean'), 
                               rating_count=('rating', 'count'))
        ratings_df.reset_index(inplace=True)
        ratings_df.columns = ['recipe_id','ratings','rating_count']
    except Exception as e:
        print("Unable to read csv file: ", REVIEW_DIR+file_name+".csv")
        print("Error: ", e)
        raise
    # Read the recipes dataframe    
    try:
        recipe_df = pd.read_csv(RECIPE_DIR+file_name+".csv", engine='python')
        recipe_df = recipe_df.drop('Unnamed: 0', axis=1)
        recipe_df['id'] = recipe_df['id'].astype(str)
    except Exception as e:
        print("Unable to read csv file: ", RECIPE_DIR+file_name+".csv")
        print("Error: ", e)
        raise
    # Join the two dataframes
    try:
        result = recipe_df.merge(ratings_df, how="left", left_on='id', right_on='recipe_id', suffixes=(False, False))
    except Exception as e:
        print("Error in joining dataframes for file: ", file_name)
        print("Error: ", e)
        raise
    # Save as the recipe file
    try:
        result.to_csv(RECIPE_DIR+file_name+".csv")
    except Exception as e:
        print("Error in Saving File: ", file_name)
        print("Error: ", e)

### Merge ratings for all initials's recipes

In [570]:
def merge_all_ratings():
    filenames = glob.glob(RECIPE_DIR+"*.csv")
    for file in filenames:
        initial = file.split('/')[-1].split('.')[0]
        try:
            merge_ratings(initial)
        except Exception as e:
            print("Error in merging for file: ", initial)
            print("Error: ", e)
            raise
    print("Successfully merged recipes with ratings!")

In [571]:
# Test / Execution
merge_all_ratings()

Successfully merged recipes with ratings!


## Combine the Recipes CSV Files

In [572]:
# Combining the recipe files into one single dataset
def combine_recipes():
    filenames = glob.glob(RECIPE_DIR+"*.csv")
    recipes_df = pd.DataFrame([], columns=recipe_columns)
    for file in filenames:
        file_df = pd.read_csv(file)
        recipes_df = pd.concat([recipes_df, file_df], ignore_index=True)
    recipes_df = recipes_df.drop(["Unnamed: 0"], axis=1)
    recipes_df.to_csv('./datasets/food_network_recipes.csv', index=False)
    print("Successfully merged recipes in 'food_network_recipes.csv'")

In [573]:
combine_recipes()

Successfully merged recipes in 'food_network_recipes.csv'


In [574]:
display(pd.read_csv('./datasets/food_network_recipes.csv'))

/tmp/ipykernel_13971/1375159316.py:1: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  display(pd.read_csv('./datasets/food_network_recipes.csv'))


id                                           name    time_taken  \
0      1947698                                    "PLT" Salad        35 min   
1      2172331  "Pearl Balls" - Pork Meatballs in Sticky Rice  12 hr 45 min   
2      1948754                           "Philly Cheesesteak"   1 hr 10 min   
3      1917222                                  "Pita" Pizzas        10 min   
4      2064412     "Please Don't Tell My Rabbi" Eggs Benedict        40 min   
...        ...                                            ...           ...   
75537  2129312                    Zuppa di Vongole: Clam Soup        40 min   
75538  1960516           Zuppa e Councesze: Soup with Mussels        45 min   
75539  1959123                          Zuzu's Peach Sparkler           NaN   
75540  1963021         Zwetschgen Datchi (Bavarian Plum Cake)           NaN   
75541  1925698                          Zydeco's 5 BBQ Shrimp        25 min   

      servings                                        ingredients  \
0            6  ['1 1/2 pounds pancetta, sliced 1/4-inch thick...   
1        About  ['One 12-ounce piece boneless, skinless pork b...   
2            4  ['1/4 cup Dijon mustard', '1/2 cup balsamic vi...   
3          NaN  ['Whole wheat pita bread', 'English muffins', ...   
4            3  ['1 large russet potato, grated, squeezed to d...   
...        ...                                                ...   
75537        4  ['2 pounds fresh clams', '1/4 cup extra-virgin...   
75538        4  ['1/2 cup/125 ml extra-virgin olive oil', '2 c...   
75539        1  ['1-1/2 oz. cognac', '1/2 oz. peach schnapps',...   
75540      NaN  ['1 piece fresh yeast', '6 1/4 tablespoons sug...   
75541        1  ['1 pound butter', '1/2 cup chopped green onio...   

                                              directions  \
0      ['Unroll the pancetta slices and cut them cros...   
1      ['Put the pork on a large cutting board and ve...   
2      ['Combine the mustard and balsamic vinegar in ...   
3      ['Spread cream cheese on pita, 1/2 an English ...   
4      ['Preheat the oven to 300 degrees F.', 'Start ...   
...                                                  ...   
75537  ['Remove excess sand from clams by soaking the...   
75538  ['Heat up 1/4 cup extra-virgin olive oil in a ...   
75539  ['In a shaker glass add the peach, mint leaves...   
75540  ['For the crust: Mix the fresh yeast with 2 ta...   
75541  ['Take the butter, cut into thirds, and melt i...   

                                              categories  recipe_id   ratings  \
0      ['Tomato Salad', 'Salad Recipes', 'Tomato', 'T...  1947698.0  5.000000   
1      ['Asian', 'Chinese Recipes', 'Meatballs', 'Ric...        NaN       NaN   
2      ['Grilled Steak', 'Grilling', 'Steak', 'Americ...  1948754.0  4.733333   
3      ['Vegetarian', 'American', 'Middle Eastern Rec...  1917222.0  4.500000   
4      ['Chorizo', 'Sausage Recipes', 'Egg Recipes', ...  2064412.0  5.000000   
...                                                  ...        ...       ...   
75537  ['Italian', 'Soup', 'Tomato', 'Clam Recipes', ...        NaN       NaN   
75538  ['Italian', 'Soup', 'Mussel', 'Shellfish Recip...        NaN       NaN   
75539  ['Liqueur Recipes', 'Gluten Free', 'Low-Fat', ...        NaN       NaN   
75540  ['Easy Dessert Recipes', 'Dessert', 'Easy Baki...  1963021.0  4.250000   
75541  ['Easy Shrimp Recipes', 'Shellfish Recipes', '...        NaN       NaN   

       rating_count  
0               3.0  
1               NaN  
2              15.0  
3               2.0  
4               1.0  
...             ...  
75537           NaN  
75538           NaN  
75539           NaN  
75540           4.0  
75541           NaN  

[75542 rows x 10 columns]

## ETL

In [38]:
fn_rv_df = pd.read_csv("datasets/food_network_reviews.csv")
fn_rv_df.head(5)

username rating               review_date  recipe_id  \
0       Cynthia P.      5  2008-08-21T22:14:08.000Z  1940340.0   
1         lynchgmr      5  2013-11-15T01:31:01.000Z  2106689.0   
2  Jim Island Girl      4  2013-09-22T17:07:50.000Z  2106689.0   
3        Rachel D.      5  2012-11-24T20:58:04.000Z  2106689.0   
4             None      5  2011-12-27T21:24:26.000Z  2106689.0   

                                         review_text  
0  Absolutely delicious...creamed corn without th...  
1  I just made this as part of a "healthy Thanksg...  
2  I did a little substituting (using regular syr...  
3  I made this for Thanksgiving this year as I ju...  
4  LOVE LOVE LOVE this recipe!!!! I wanted to hav...

In [61]:
display(fn_rv_df[fn_rv_df['review_date'] == None])

Empty DataFrame
Columns: [username, rating, review_date, recipe_id, review_text]
Index: []

In [58]:
fn_rv = fn_rv_df.copy()
fn_rv = fn_rv[['username','recipe_id','review_date', 'rating', 'review_text']]
fn_rv.columns = ['user_id', 'recipe_id', 'date', 'rating', 'review']
fn_rv = fn_rv[fn_rv['recipe_id'].notnull()]
fn_rv['recipe_id'] = fn_rv['recipe_id'].apply(lambda x: str(int(x)))
fn_rv['rating'] = fn_rv['rating'].fillna(0)
display(fn_rv)

user_id recipe_id                      date rating  \
0          Cynthia P.   1940340  2008-08-21T22:14:08.000Z      5   
1            lynchgmr   2106689  2013-11-15T01:31:01.000Z      5   
2     Jim Island Girl   2106689  2013-09-22T17:07:50.000Z      4   
3           Rachel D.   2106689  2012-11-24T20:58:04.000Z      5   
4                None   2106689  2011-12-27T21:24:26.000Z      5   
...               ...       ...                       ...    ...   
9297         charlieO   2124326  2010-10-21T12:22:43.000Z      5   
9298             None   2047697  2014-06-12T20:44:42.000Z      5   
9299             None   2047697  2012-12-22T08:09:43.000Z      5   
9300         djscotec   2047697  2012-01-15T14:07:44.000Z      5   
9301    bookpusher700   2047697  2011-11-25T13:01:39.000Z      5   

                                                 review  
0     Absolutely delicious...creamed corn without th...  
1     I just made this as part of a "healthy Thanksg...  
2     I did a little substituting (using regular syr...  
3     I made this for Thanksgiving this year as I ju...  
4     LOVE LOVE LOVE this recipe!!!! I wanted to hav...  
...                                                 ...  
9297  After watching the Tailgate Warriors I was won...  
9298  I haven't tried it yet, but I'm curious - it s...  
9299  We actually have done this every year for many...  
9300  Robert you are a tailgating genius!  This is j...  
9301  Quick and easy.  Having the men do this turkey...  

[9081 rows x 5 columns]

In [6]:
fn_rc_df = pd.read_csv("datasets/food_network_recipes.csv")
fn_rc_df.head(5)

id                                               name   time_taken  \
0  1940225                  "We Need to Talk" Chocolate Pizza       10 min   
1  8613916               "What You Got" Meatloaf on the Grill  1 hr 20 min   
2  2085413  "What am I...?" Chopped Liver with Schmaltz Fr...       40 min   
3  3414490                   "Who Will Love Me As I Yam?" Pie  1 hr 20 min   
4  1947492  (Web Exclusive) Round 2 Recipe: Bean Chili Que...       22 min   

  servings                                        ingredients  \
0        1  ['1/2 recipe Basic Pizza Dough, recipe follows...   
1        4  ['1 cup ketchup', '1/3 cup light brown sugar',...   
2       12  ['Reserved skin from 1 chicken, about 1 cup', ...   
3        8  ['Bourbon Marshmallows:', 'Nonstick cooking sp...   
4        2  ['4 (8-inch) flour tortillas', '1/2 cup shredd...   

                                          directions  \
0  ['Preheat oven to 400 degrees F.', 'After baki...   
1  ['For the glaze: In a medium bowl, add the ket...   
2  ['In a skillet over medium heat, saute the chi...   
3  ["For the bourbon marshmallows: Spray a 9-by-1...   
4  ['Heat a large skillet over medium-high heat.'...   

                                          categories  
0  ['Easy Dessert Recipes', 'Dessert', 'Easy Baki...  
1              ['Meatloaf', 'Main Dish', 'Grilling']  
2  ['Easy Chicken', 'Chicken Recipes', 'Poultry',...  
3                  ['Pie Recipes', 'Yam', 'Dessert']  
4  ['Quesadilla', 'Beans and Legumes', 'Main Dish...

In [1]:
# Characters to be deleted
delete_char = ['(',')','[',']','/','-','⁄','%','.','\n']

# Extra keywords to be omitted
extras = [
    'bag',
    'box',
    'bunch',
    'can',
    'cup',
    'cups',
    'dash',
    'dozen',
    'drop',
    'envelope',
    'fluid',
    'g',
    'gallon',
    'head',
    'inch',
    'jar',
    'kg',
    'kgs',
    'large',
    'lb',
    'lbs',
    'leaf',
    'liter',
    'loaf',
    'medium',
    'ml',
    'ounce',
    'ounces',
    'package',
    'packages',
    'packet',
    'packets',
    'pinch',
    'pint',
    'pints',
    'quart',
    'quarts',
    'scoop',
    'scoops',
    'sheet',
    'sheets',
    'slice',
    'slices',
    'small',
    'sprig',
    'sprigs',
    'stalk',
    'stalks',
    'tablespoon',
    'tablespoons',
    'teaspoon',
    'teaspoons',
    'whole'
]

# Remove the extra tokens
def remove_extras(string):
    
    string = str(string)
    for char in delete_char:
        string = string.replace(str(char), " ")
    
    tokens = string.split(" ")
    
    if tokens[0].strip().lower() == 'for':
        return ""
    
    string_list=[]
    for token in tokens:
        token = token.strip()
        if not token.isnumeric():
            if token not in extras:
                string_list.append(token)
    
    return (' '.join([elem for elem in string_list])).strip()

In [21]:
# Process the dataframe to transform ingredients
def process_ingredients(input_df):
    ingredients = input_df.copy()
    ingredients = ingredients[['ingredients','id']]
    ingredients['ingredients'] = ingredients['ingredients'].apply(ast.literal_eval)
    ingredients = ingredients.explode('ingredients')
    ingredients = ingredients.dropna()
    ingredients['ingredients'] = ingredients['ingredients'].str.lower()
    ingredients['ingredients'] = ingredients['ingredients'].apply(remove_extras)
    ingredients = ingredients[ingredients["ingredients"] != ""]
    ingredients = ingredients.groupby(['id']).agg({'ingredients': lambda x: x.tolist()})
    ingredients = ingredients[ingredients['ingredients'] != ""]
    ingredients['ingredients'] = ingredients['ingredients'].astype(str)
    ingredients.reset_index(inplace=True)
    return ingredients

In [31]:
def segregate(x):
    minutes = 0;
    x = x.strip()
    tokens = x.split(" ")
    for i in range(len(tokens)):
        token = tokens[i].strip()
        if i%2 != 0:
            if token == "hr":
                minutes += int(tokens[i-1].strip()) * 60
            elif token == "min":
                minutes += int(tokens[i-1].strip())
    return str(minutes)

def process_time(input_df):
    time_taken = input_df.copy()
    time_taken['time_taken'] = time_taken['time_taken'].astype(str).apply(segregate)
    return time_taken

In [35]:
def num_count(input_df):
    num_df = input_df.copy()
    num_df['directions'] = num_df['directions'].apply(ast.literal_eval)
    num_df['n_steps'] = num_df['directions'].apply(lambda x: len(x))
    num_df['directions'] = num_df['directions'].astype(str)
    num_df['ingredients'] = num_df['ingredients'].apply(ast.literal_eval)
    num_df['n_ingredients'] = num_df['ingredients'].apply(lambda x: len(x))
    num_df['ingredients'] = num_df['ingredients'].astype(str)
    return num_df

In [36]:
fn_rc_ig = fn_rc_df.copy()
fn_rc_ig = process_ingredients(fn_rc_ig)
fn_rc_ig.columns = ['r_id', 'ing']
fn_rc = pd.merge(fn_rc_df, fn_rc_ig, how='left', left_on=["id"], right_on=["r_id"])
fn_rc['ingredients'] = fn_rc['ing']
fn_rc = fn_rc.drop(['r_id', 'ing'], axis=1)
fn_rc['ingredients'] = fn_rc['ingredients'].fillna("[]")
fn_rc = process_time(fn_rc)
fn_rc = num_count(fn_rc)
display(fn_rc)

id                                               name time_taken  \
0      1940225                  "We Need to Talk" Chocolate Pizza         10   
1      8613916               "What You Got" Meatloaf on the Grill         80   
2      2085413  "What am I...?" Chopped Liver with Schmaltz Fr...         40   
3      3414490                   "Who Will Love Me As I Yam?" Pie         80   
4      1947492  (Web Exclusive) Round 2 Recipe: Bean Chili Que...         22   
...        ...                                                ...        ...   
75537  1938900             Myrna's Toasted Coconut-Chocolate Bars         50   
75538  1940002                                  Mystery Meat Loaf        100   
75539  1910928                                 Mystery Mocha Cake         60   
75540  2593846                                      Mystery Rolls         20   
75541  2103110                              Mystery of the Orient        240   

      servings                                        ingredients  \
0            1  ['recipe basic pizza dough, recipe follows', '...   
1            4  ['ketchup', 'light brown sugar', 'worcestershi...   
2           12  ['reserved skin from chicken, about', 'onion, ...   
3            8  ['bourbon marshmallows:', 'nonstick cooking sp...   
4            2  ['flour tortillas', 'shredded jack cheese', 'b...   
...        ...                                                ...   
75537       50  ['heaping sugar', 'scant egg whites  from abou...   
75538        6  ['pounds ground round beef  percent lean', 'se...   
75539        9  ['unsweetened chocolate', 'butter', 'sugar', '...   
75540        8  ['stick   butter', 'crumbled blue cheese', 'fl...   
75541        1  ['pounds bittersweet chocolate, tempered', 'wh...   

                                              directions  \
0      ['Preheat oven to 400 degrees F.', 'After baki...   
1      ['For the glaze: In a medium bowl, add the ket...   
2      ['In a skillet over medium heat, saute the chi...   
3      ["For the bourbon marshmallows: Spray a 9-by-1...   
4      ['Heat a large skillet over medium-high heat.'...   
...                                                  ...   
75537  ['Heat the oven to 350 degrees F. Mix the suga...   
75538  ['Preheat oven to 350 degrees. In a large bowl...   
75539  ['Preheat oven to 350 degrees F.', 'Melt the c...   
75540  ['Preheat the oven to 350 degrees F.', 'Put th...   
75541  ['Make the base: Use flexible aluminum strips ...   

                                              categories  n_steps  \
0      ['Easy Dessert Recipes', 'Dessert', 'Easy Baki...       15   
1                  ['Meatloaf', 'Main Dish', 'Grilling']        9   
2      ['Easy Chicken', 'Chicken Recipes', 'Poultry',...        2   
3                      ['Pie Recipes', 'Yam', 'Dessert']        8   
4      ['Quesadilla', 'Beans and Legumes', 'Main Dish...        4   
...                                                  ...      ...   
75537  ['Chocolate Cookie Recipes', 'Cookie', 'Baking...        2   
75538  ['Easy Main Dish', 'Main Dish', 'Meatloaf', 'B...        1   
75539  ['Easy Dessert Recipes', 'Dessert', 'Chocolate...        2   
75540  ['Bread', 'Blue Cheese', 'Side Dish', 'Appetiz...        4   
75541  ['French Recipes', 'European Recipes', 'Dessert']        3   

       n_ingredients  
0                 13  
1                 20  
2                  6  
3                 26  
4                 13  
...              ...  
75537              5  
75538              7  
75539             11  
75540              3  
75541              7  

[75542 rows x 9 columns]

In [45]:
fn_rc_copy = fn_rc.copy()
fn_rc_copy = fn_rc_copy.drop(['servings'], axis=1)
r_columns = [
    'id', 
    'name', 
    'minutes', 
    'ingredients',
    'steps',
    'tags',
    'n_steps',
    'n_ingredients'
]
fn_rc_copy.columns = r_columns
display(fn_rc_copy)

id                                               name minutes  \
0      1940225                  "We Need to Talk" Chocolate Pizza      10   
1      8613916               "What You Got" Meatloaf on the Grill      80   
2      2085413  "What am I...?" Chopped Liver with Schmaltz Fr...      40   
3      3414490                   "Who Will Love Me As I Yam?" Pie      80   
4      1947492  (Web Exclusive) Round 2 Recipe: Bean Chili Que...      22   
...        ...                                                ...     ...   
75537  1938900             Myrna's Toasted Coconut-Chocolate Bars      50   
75538  1940002                                  Mystery Meat Loaf     100   
75539  1910928                                 Mystery Mocha Cake      60   
75540  2593846                                      Mystery Rolls      20   
75541  2103110                              Mystery of the Orient     240   

                                             ingredients  \
0      ['recipe basic pizza dough, recipe follows', '...   
1      ['ketchup', 'light brown sugar', 'worcestershi...   
2      ['reserved skin from chicken, about', 'onion, ...   
3      ['bourbon marshmallows:', 'nonstick cooking sp...   
4      ['flour tortillas', 'shredded jack cheese', 'b...   
...                                                  ...   
75537  ['heaping sugar', 'scant egg whites  from abou...   
75538  ['pounds ground round beef  percent lean', 'se...   
75539  ['unsweetened chocolate', 'butter', 'sugar', '...   
75540  ['stick   butter', 'crumbled blue cheese', 'fl...   
75541  ['pounds bittersweet chocolate, tempered', 'wh...   

                                                   steps  \
0      ['Preheat oven to 400 degrees F.', 'After baki...   
1      ['For the glaze: In a medium bowl, add the ket...   
2      ['In a skillet over medium heat, saute the chi...   
3      ["For the bourbon marshmallows: Spray a 9-by-1...   
4      ['Heat a large skillet over medium-high heat.'...   
...                                                  ...   
75537  ['Heat the oven to 350 degrees F. Mix the suga...   
75538  ['Preheat oven to 350 degrees. In a large bowl...   
75539  ['Preheat oven to 350 degrees F.', 'Melt the c...   
75540  ['Preheat the oven to 350 degrees F.', 'Put th...   
75541  ['Make the base: Use flexible aluminum strips ...   

                                                    tags  n_steps  \
0      ['Easy Dessert Recipes', 'Dessert', 'Easy Baki...       15   
1                  ['Meatloaf', 'Main Dish', 'Grilling']        9   
2      ['Easy Chicken', 'Chicken Recipes', 'Poultry',...        2   
3                      ['Pie Recipes', 'Yam', 'Dessert']        8   
4      ['Quesadilla', 'Beans and Legumes', 'Main Dish...        4   
...                                                  ...      ...   
75537  ['Chocolate Cookie Recipes', 'Cookie', 'Baking...        2   
75538  ['Easy Main Dish', 'Main Dish', 'Meatloaf', 'B...        1   
75539  ['Easy Dessert Recipes', 'Dessert', 'Chocolate...        2   
75540  ['Bread', 'Blue Cheese', 'Side Dish', 'Appetiz...        4   
75541  ['French Recipes', 'European Recipes', 'Dessert']        3   

       n_ingredients  
0                 13  
1                 20  
2                  6  
3                 26  
4                 13  
...              ...  
75537              5  
75538              7  
75539             11  
75540              3  
75541              7  

[75542 rows x 8 columns]

In [60]:
if not os.path.exists("temp/"):
        os.makedirs("temp/")
fn_rc.to_csv('temp/food_network_recipes.csv', index=False)
fn_rv.to_csv('temp/food_network_reviews.csv', index=False)

# FIN